In [1]:
import os
import sys
import random
from time import time

import pandas as pd
from tqdm import tqdm

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

from argparse import Namespace
from utils.log_helper import *
from utils.metrics import *
from utils.model_helper import *
from data_loader.loader_kgat import DataLoaderKGAT
from KGAT import *

In [2]:
def evaluate(model, dataloader, Ks, device):
    test_batch_size = dataloader.test_batch_size
    train_user_dict = dataloader.train_user_dict
    test_user_dict = dataloader.test_user_dict

    model.eval()

    user_ids = list(test_user_dict.keys())
    user_ids_batches = [user_ids[i: i + test_batch_size] for i in range(0, len(user_ids), test_batch_size)]
    user_ids_batches = [torch.LongTensor(d) for d in user_ids_batches]

    n_items = dataloader.n_items
    item_ids = torch.arange(n_items, dtype=torch.long).to(device)

    cf_scores = []
    metric_names = ['precision', 'recall', 'ndcg']
    metrics_dict = {k: {m: [] for m in metric_names} for k in Ks}

    with tqdm(total=len(user_ids_batches), desc='Evaluating Iteration') as pbar:
        for batch_user_ids in user_ids_batches:
            batch_user_ids = batch_user_ids.to(device)

            with torch.no_grad():
                batch_scores = model(batch_user_ids, item_ids, mode='predict')       # (n_batch_users, n_items)

            batch_scores = batch_scores.cpu()
            batch_metrics = calc_metrics_at_k(batch_scores, train_user_dict, test_user_dict, batch_user_ids.cpu().numpy(), item_ids.cpu().numpy(), Ks)

            cf_scores.append(batch_scores.numpy())
            for k in Ks:
                for m in metric_names:
                    metrics_dict[k][m].append(batch_metrics[k][m])
            pbar.update(1)

    cf_scores = np.concatenate(cf_scores, axis=0)
    for k in Ks:
        for m in metric_names:
            metrics_dict[k][m] = np.concatenate(metrics_dict[k][m]).mean()
    return cf_scores, metrics_dict

In [3]:
#remove pretrain
def train(args):
    # seed
    random.seed(args.seed)
    np.random.seed(args.seed)
    torch.manual_seed(args.seed)
    torch.cuda.manual_seed_all(args.seed)

    log_save_id = create_log_id(args.save_dir)
    logging_config(folder=args.save_dir, name='log{:d}'.format(log_save_id), no_console=False)
    logging.info(args)

    # GPU / CPU
    device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

    # load data
    data = DataLoaderKGAT(args, logging)
    
    # construct model & optimizer
    model = KGAT(args, data.n_users, data.n_entities, data.n_relations, data.A_in) #A_in : Adjacency matrix
    model.to(device)
    logging.info(model)

    cf_optimizer = optim.Adam(model.parameters(), lr=args.lr)
    kg_optimizer = optim.Adam(model.parameters(), lr=args.lr)

    # initialize metrics
    best_epoch = -1
    best_recall = 0

    Ks = eval(args.Ks)
    k_min = min(Ks)
    k_max = max(Ks)

    epoch_list = []
    metrics_list = {k: {'precision': [], 'recall': [], 'ndcg': []} for k in Ks}

    # train model
    for epoch in range(1, args.n_epoch + 1):
        time0 = time()
        model.train()

        # train cf
        time1 = time()
        cf_total_loss = 0
        n_cf_batch = data.n_cf_train // data.cf_batch_size + 1

        for iter in range(1, n_cf_batch + 1):
            time2 = time()
            cf_batch_user, cf_batch_pos_item, cf_batch_neg_item = data.generate_cf_batch(data.train_user_dict, data.cf_batch_size)
            cf_batch_user = cf_batch_user.to(device)
            cf_batch_pos_item = cf_batch_pos_item.to(device)
            cf_batch_neg_item = cf_batch_neg_item.to(device)

            cf_batch_loss = model(cf_batch_user, cf_batch_pos_item, cf_batch_neg_item, mode='train_cf')

            if np.isnan(cf_batch_loss.cpu().detach().numpy()):
                logging.info('ERROR (CF Training): Epoch {:04d} Iter {:04d} / {:04d} Loss is nan.'.format(epoch, iter, n_cf_batch))
                sys.exit()

            cf_batch_loss.backward()
            cf_optimizer.step()
            cf_optimizer.zero_grad()
            cf_total_loss += cf_batch_loss.item()

            if (iter % args.cf_print_every) == 0:
                logging.info('CF Training: Epoch {:04d} Iter {:04d} / {:04d} | Time {:.1f}s | Iter Loss {:.4f} | Iter Mean Loss {:.4f}'.format(epoch, iter, n_cf_batch, time() - time2, cf_batch_loss.item(), cf_total_loss / iter))
        logging.info('CF Training: Epoch {:04d} Total Iter {:04d} | Total Time {:.1f}s | Iter Mean Loss {:.4f}'.format(epoch, n_cf_batch, time() - time1, cf_total_loss / n_cf_batch))

        # train kg
        time3 = time()
        kg_total_loss = 0
        n_kg_batch = data.n_kg_train // data.kg_batch_size + 1

        for iter in range(1, n_kg_batch + 1):
            time4 = time()
            kg_batch_head, kg_batch_relation, kg_batch_pos_tail, kg_batch_neg_tail = data.generate_kg_batch(data.train_kg_dict, data.kg_batch_size, data.n_users_entities)
            kg_batch_head = kg_batch_head.to(device)
            kg_batch_relation = kg_batch_relation.to(device)
            kg_batch_pos_tail = kg_batch_pos_tail.to(device)
            kg_batch_neg_tail = kg_batch_neg_tail.to(device)

            kg_batch_loss = model(kg_batch_head, kg_batch_relation, kg_batch_pos_tail, kg_batch_neg_tail, mode='train_kg')

            if np.isnan(kg_batch_loss.cpu().detach().numpy()):
                logging.info('ERROR (KG Training): Epoch {:04d} Iter {:04d} / {:04d} Loss is nan.'.format(epoch, iter, n_kg_batch))
                sys.exit()

            kg_batch_loss.backward()
            kg_optimizer.step()
            kg_optimizer.zero_grad()
            kg_total_loss += kg_batch_loss.item()

            if (iter % args.kg_print_every) == 0:
                logging.info('KG Training: Epoch {:04d} Iter {:04d} / {:04d} | Time {:.1f}s | Iter Loss {:.4f} | Iter Mean Loss {:.4f}'.format(epoch, iter, n_kg_batch, time() - time4, kg_batch_loss.item(), kg_total_loss / iter))
        logging.info('KG Training: Epoch {:04d} Total Iter {:04d} | Total Time {:.1f}s | Iter Mean Loss {:.4f}'.format(epoch, n_kg_batch, time() - time3, kg_total_loss / n_kg_batch))

        # update attention
        time5 = time()
        h_list = data.h_list.to(device)
        t_list = data.t_list.to(device)
        r_list = data.r_list.to(device)
        relations = list(data.laplacian_dict.keys())
        model(h_list, t_list, r_list, relations, mode='update_att')
        logging.info('Update Attention: Epoch {:04d} | Total Time {:.1f}s'.format(epoch, time() - time5))

        logging.info('CF + KG Training: Epoch {:04d} | Total Time {:.1f}s'.format(epoch, time() - time0))

        # evaluate cf
        if (epoch % args.evaluate_every) == 0 or epoch == args.n_epoch:
            time6 = time()
            _, metrics_dict = evaluate(model, data, Ks, device)
            logging.info('CF Evaluation: Epoch {:04d} | Total Time {:.1f}s | Precision [{:.4f}, {:.4f}], Recall [{:.4f}, {:.4f}], NDCG [{:.4f}, {:.4f}]'.format(
                epoch, time() - time6, metrics_dict[k_min]['precision'], metrics_dict[k_max]['precision'], metrics_dict[k_min]['recall'], metrics_dict[k_max]['recall'], metrics_dict[k_min]['ndcg'], metrics_dict[k_max]['ndcg']))

            epoch_list.append(epoch)
            for k in Ks:
                for m in ['precision', 'recall', 'ndcg']:
                    metrics_list[k][m].append(metrics_dict[k][m])
            best_recall, should_stop = early_stopping(metrics_list[k_min]['recall'], args.stopping_steps)

            if should_stop:
                break

            if metrics_list[k_min]['recall'].index(best_recall) == len(epoch_list) - 1:
                save_model(model, args.save_dir, epoch, best_epoch)
                logging.info('Save model on epoch {:04d}!'.format(epoch))
                best_epoch = epoch

    # save metrics
    metrics_df = [epoch_list]
    metrics_cols = ['epoch_idx']
    for k in Ks:
        for m in ['precision', 'recall', 'ndcg']:
            metrics_df.append(metrics_list[k][m])
            metrics_cols.append('{}@{}'.format(m, k))
    metrics_df = pd.DataFrame(metrics_df).transpose()
    metrics_df.columns = metrics_cols
    metrics_df.to_csv(args.save_dir + '/metrics.tsv', sep='\t', index=False)

    # print best metrics
    best_metrics = metrics_df.loc[metrics_df['epoch_idx'] == best_epoch].iloc[0].to_dict()
    logging.info('Best CF Evaluation: Epoch {:04d} | Precision [{:.4f}, {:.4f}], Recall [{:.4f}, {:.4f}], NDCG [{:.4f}, {:.4f}]'.format(
        int(best_metrics['epoch_idx']), best_metrics['precision@{}'.format(k_min)], best_metrics['precision@{}'.format(k_max)], best_metrics['recall@{}'.format(k_min)], best_metrics['recall@{}'.format(k_max)], best_metrics['ndcg@{}'.format(k_min)], best_metrics['ndcg@{}'.format(k_max)]))

In [4]:
def predict(args):
    # GPU / CPU
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

    # load data
    data = DataLoaderKGAT(args, logging)

    # load model
    model = KGAT(args, data.n_users, data.n_entities, data.n_relations)
    model = load_model(model, args.save_dir+'/model_last.pth')
    model.to(device)

    # predict
    Ks = eval(args.Ks)
    k_min = min(Ks)
    k_max = max(Ks)

    cf_scores, metrics_dict = evaluate(model, data, Ks, device)
    np.save(args.save_dir + '/cf_scores.npy', cf_scores)
    print('CF Evaluation: Precision [{:.4f}, {:.4f}], Recall [{:.4f}, {:.4f}], NDCG [{:.4f}, {:.4f}]'.format(
        metrics_dict[k_min]['precision'], metrics_dict[k_max]['precision'], metrics_dict[k_min]['recall'], metrics_dict[k_max]['recall'], metrics_dict[k_min]['ndcg'], metrics_dict[k_max]['ndcg']))

In [7]:
args = Namespace(
    seed = 0,
    data_name = 'culture',
    data_dir = 'datasets/',
    cf_batch_size =512,
    kg_batch_size = 512,
    test_batch_size = 10000,
    embed_dim = 128,
    relation_dim = 128,
    laplacian_type = 'random-walk',
    aggregation_type = 'bi-interaction',
    conv_dim_list = '[64, 32, 16]',
    mess_dropout = '[0.1, 0.1, 0.1]',
    kg_l2loss_lambda = 1e-5,
    cf_l2loss_lambda = 1e-5,
    lr = 0.001,
    n_epoch = 300,
    stopping_steps = 30,
    cf_print_every = 1,
    kg_print_every = 1,
    evaluate_every = 10,
    Ks = '[10, 20, 40, 80, 100]'
)
save_dir = 'trained_model/culture'
args.save_dir = save_dir
if not os.path.exists(save_dir):
    os.makedirs(save_dir)

train(args)
predict(args)

2023-10-13 10:16:27,827 - root - INFO - Namespace(seed=0, data_name='culture', data_dir='datasets/', cf_batch_size=512, kg_batch_size=512, test_batch_size=10000, embed_dim=128, relation_dim=128, laplacian_type='random-walk', aggregation_type='bi-interaction', conv_dim_list='[64, 32, 16]', mess_dropout='[0.1, 0.1, 0.1]', kg_l2loss_lambda=1e-05, cf_l2loss_lambda=1e-05, lr=0.001, n_epoch=300, stopping_steps=30, cf_print_every=1, kg_print_every=1, evaluate_every=10, Ks='[10, 20, 40, 80, 100]', save_dir='trained_model/culture')


All logs will be saved to trained_model/culture/log19.log


2023-10-13 10:16:28,171 - root - INFO - n_users:           1835
2023-10-13 10:16:28,171 - root - INFO - n_items:           206
2023-10-13 10:16:28,172 - root - INFO - n_entities:        410
2023-10-13 10:16:28,172 - root - INFO - n_users_entities:  2245
2023-10-13 10:16:28,172 - root - INFO - n_relations:       24
2023-10-13 10:16:28,173 - root - INFO - n_h_list:          15046
2023-10-13 10:16:28,173 - root - INFO - n_t_list:          15046
2023-10-13 10:16:28,173 - root - INFO - n_r_list:          15046
2023-10-13 10:16:28,173 - root - INFO - n_cf_train:        5484
2023-10-13 10:16:28,174 - root - INFO - n_cf_test:         3661
2023-10-13 10:16:28,174 - root - INFO - n_kg_train:        15046
/home/user/ETRI-Recommender/data_loader/loader_kgat.py:118: RuntimeWarning: divide by zero encountered in power
  d_inv = np.power(rowsum, -1.0).flatten()
2023-10-13 10:16:28,208 - root - INFO - KGAT(
  (entity_user_embed): Embedding(2245, 128)
  (relation_embed): Embedding(24, 128)
  (aggregato

2023-10-13 10:16:29,057 - root - INFO - CF Training: Epoch 0002 Iter 0004 / 0011 | Time 0.0s | Iter Loss 0.5278 | Iter Mean Loss 0.5508
2023-10-13 10:16:29,089 - root - INFO - CF Training: Epoch 0002 Iter 0005 / 0011 | Time 0.0s | Iter Loss 0.5090 | Iter Mean Loss 0.5425
2023-10-13 10:16:29,113 - root - INFO - CF Training: Epoch 0002 Iter 0006 / 0011 | Time 0.0s | Iter Loss 0.4712 | Iter Mean Loss 0.5306
2023-10-13 10:16:29,132 - root - INFO - CF Training: Epoch 0002 Iter 0007 / 0011 | Time 0.0s | Iter Loss 0.4590 | Iter Mean Loss 0.5204
2023-10-13 10:16:29,168 - root - INFO - CF Training: Epoch 0002 Iter 0008 / 0011 | Time 0.0s | Iter Loss 0.4568 | Iter Mean Loss 0.5124
2023-10-13 10:16:29,201 - root - INFO - CF Training: Epoch 0002 Iter 0009 / 0011 | Time 0.0s | Iter Loss 0.4475 | Iter Mean Loss 0.5052
2023-10-13 10:16:29,225 - root - INFO - CF Training: Epoch 0002 Iter 0010 / 0011 | Time 0.0s | Iter Loss 0.4346 | Iter Mean Loss 0.4981
2023-10-13 10:16:29,266 - root - INFO - CF Train

2023-10-13 10:16:30,049 - root - INFO - KG Training: Epoch 0003 Iter 0009 / 0030 | Time 0.0s | Iter Loss 0.1271 | Iter Mean Loss 0.1316
2023-10-13 10:16:30,060 - root - INFO - KG Training: Epoch 0003 Iter 0010 / 0030 | Time 0.0s | Iter Loss 0.1398 | Iter Mean Loss 0.1324
2023-10-13 10:16:30,088 - root - INFO - KG Training: Epoch 0003 Iter 0011 / 0030 | Time 0.0s | Iter Loss 0.1182 | Iter Mean Loss 0.1311
2023-10-13 10:16:30,104 - root - INFO - KG Training: Epoch 0003 Iter 0012 / 0030 | Time 0.0s | Iter Loss 0.1174 | Iter Mean Loss 0.1300
2023-10-13 10:16:30,117 - root - INFO - KG Training: Epoch 0003 Iter 0013 / 0030 | Time 0.0s | Iter Loss 0.1219 | Iter Mean Loss 0.1294
2023-10-13 10:16:30,129 - root - INFO - KG Training: Epoch 0003 Iter 0014 / 0030 | Time 0.0s | Iter Loss 0.1047 | Iter Mean Loss 0.1276
2023-10-13 10:16:30,141 - root - INFO - KG Training: Epoch 0003 Iter 0015 / 0030 | Time 0.0s | Iter Loss 0.1110 | Iter Mean Loss 0.1265
2023-10-13 10:16:30,153 - root - INFO - KG Train

...

2023-10-13 10:20:06,298 - root - INFO - KG Training: Epoch 0295 Iter 0025 / 0030 | Time 0.0s | Iter Loss 0.0004 | Iter Mean Loss 0.0023
2023-10-13 10:20:06,310 - root - INFO - KG Training: Epoch 0295 Iter 0026 / 0030 | Time 0.0s | Iter Loss 0.0009 | Iter Mean Loss 0.0023
2023-10-13 10:20:06,337 - root - INFO - KG Training: Epoch 0295 Iter 0027 / 0030 | Time 0.0s | Iter Loss 0.0122 | Iter Mean Loss 0.0026
2023-10-13 10:20:06,353 - root - INFO - KG Training: Epoch 0295 Iter 0028 / 0030 | Time 0.0s | Iter Loss 0.0023 | Iter Mean Loss 0.0026
2023-10-13 10:20:06,374 - root - INFO - KG Training: Epoch 0295 Iter 0029 / 0030 | Time 0.0s | Iter Loss 0.0007 | Iter Mean Loss 0.0025
2023-10-13 10:20:06,390 - root - INFO - KG Training: Epoch 0295 Iter 0030 / 0030 | Time 0.0s | Iter Loss 0.0011 | Iter Mean Loss 0.0025
2023-10-13 10:20:06,390 - root - INFO - KG Training: Epoch 0295 Total Iter 0030 | Total Time 0.5s | Iter Mean Loss 0.0025
2023-10-13 10:20:06,398 - root - INFO - Update Attention: Epoc

2023-10-13 10:20:07,329 - root - INFO - CF Training: Epoch 0297 Iter 0009 / 0011 | Time 0.0s | Iter Loss 0.0067 | Iter Mean Loss 0.0075
2023-10-13 10:20:07,350 - root - INFO - CF Training: Epoch 0297 Iter 0010 / 0011 | Time 0.0s | Iter Loss 0.0077 | Iter Mean Loss 0.0075
2023-10-13 10:20:07,372 - root - INFO - CF Training: Epoch 0297 Iter 0011 / 0011 | Time 0.0s | Iter Loss 0.0078 | Iter Mean Loss 0.0075
2023-10-13 10:20:07,372 - root - INFO - CF Training: Epoch 0297 Total Iter 0011 | Total Time 0.2s | Iter Mean Loss 0.0075
2023-10-13 10:20:07,387 - root - INFO - KG Training: Epoch 0297 Iter 0001 / 0030 | Time 0.0s | Iter Loss 0.0004 | Iter Mean Loss 0.0004
2023-10-13 10:20:07,400 - root - INFO - KG Training: Epoch 0297 Iter 0002 / 0030 | Time 0.0s | Iter Loss 0.0010 | Iter Mean Loss 0.0007
2023-10-13 10:20:07,412 - root - INFO - KG Training: Epoch 0297 Iter 0003 / 0030 | Time 0.0s | Iter Loss 0.0004 | Iter Mean Loss 0.0006
2023-10-13 10:20:07,424 - root - INFO - KG Training: Epoch 029

2023-10-13 10:20:08,328 - root - INFO - KG Training: Epoch 0298 Iter 0014 / 0030 | Time 0.0s | Iter Loss 0.0004 | Iter Mean Loss 0.0020
2023-10-13 10:20:08,356 - root - INFO - KG Training: Epoch 0298 Iter 0015 / 0030 | Time 0.0s | Iter Loss 0.0004 | Iter Mean Loss 0.0019
2023-10-13 10:20:08,372 - root - INFO - KG Training: Epoch 0298 Iter 0016 / 0030 | Time 0.0s | Iter Loss 0.0004 | Iter Mean Loss 0.0018
2023-10-13 10:20:08,385 - root - INFO - KG Training: Epoch 0298 Iter 0017 / 0030 | Time 0.0s | Iter Loss 0.0005 | Iter Mean Loss 0.0017
2023-10-13 10:20:08,410 - root - INFO - KG Training: Epoch 0298 Iter 0018 / 0030 | Time 0.0s | Iter Loss 0.0004 | Iter Mean Loss 0.0016
2023-10-13 10:20:08,425 - root - INFO - KG Training: Epoch 0298 Iter 0019 / 0030 | Time 0.0s | Iter Loss 0.0004 | Iter Mean Loss 0.0016
2023-10-13 10:20:08,437 - root - INFO - KG Training: Epoch 0298 Iter 0020 / 0030 | Time 0.0s | Iter Loss 0.0004 | Iter Mean Loss 0.0015
2023-10-13 10:20:08,450 - root - INFO - KG Train

2023-10-13 10:20:09,362 - root - INFO - KG Training: Epoch 0299 Total Iter 0030 | Total Time 0.5s | Iter Mean Loss 0.0011
2023-10-13 10:20:09,370 - root - INFO - Update Attention: Epoch 0299 | Total Time 0.0s
2023-10-13 10:20:09,371 - root - INFO - CF + KG Training: Epoch 0299 | Total Time 0.8s
2023-10-13 10:20:09,409 - root - INFO - CF Training: Epoch 0300 Iter 0001 / 0011 | Time 0.0s | Iter Loss 0.0074 | Iter Mean Loss 0.0074
2023-10-13 10:20:09,444 - root - INFO - CF Training: Epoch 0300 Iter 0002 / 0011 | Time 0.0s | Iter Loss 0.0073 | Iter Mean Loss 0.0073
2023-10-13 10:20:09,470 - root - INFO - CF Training: Epoch 0300 Iter 0003 / 0011 | Time 0.0s | Iter Loss 0.0074 | Iter Mean Loss 0.0074
2023-10-13 10:20:09,493 - root - INFO - CF Training: Epoch 0300 Iter 0004 / 0011 | Time 0.0s | Iter Loss 0.0075 | Iter Mean Loss 0.0074
2023-10-13 10:20:09,515 - root - INFO - CF Training: Epoch 0300 Iter 0005 / 0011 | Time 0.0s | Iter Loss 0.0068 | Iter Mean Loss 0.0073
2023-10-13 10:20:09,537 

CF Evaluation: Precision [0.0859, 0.0180], Recall [0.4300, 0.9005], NDCG [0.2815, 0.4009]


In [9]:
args.Ks = '[2, 10]'
predict(args)

2023-10-13 10:20:49,355 - root - INFO - n_users:           1835
2023-10-13 10:20:49,356 - root - INFO - n_items:           206
2023-10-13 10:20:49,357 - root - INFO - n_entities:        410
2023-10-13 10:20:49,358 - root - INFO - n_users_entities:  2245
2023-10-13 10:20:49,359 - root - INFO - n_relations:       24
2023-10-13 10:20:49,360 - root - INFO - n_h_list:          15046
2023-10-13 10:20:49,360 - root - INFO - n_t_list:          15046
2023-10-13 10:20:49,361 - root - INFO - n_r_list:          15046
2023-10-13 10:20:49,362 - root - INFO - n_cf_train:        5484
2023-10-13 10:20:49,362 - root - INFO - n_cf_test:         3661
2023-10-13 10:20:49,364 - root - INFO - n_kg_train:        15046
/home/user/ETRI-Recommender/data_loader/loader_kgat.py:118: RuntimeWarning: divide by zero encountered in power
  d_inv = np.power(rowsum, -1.0).flatten()
Evaluating Iteration: 100%|███████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 15.43it/s]

CF Evaluation: Precision [0.1493, 0.0859], Recall [0.1493, 0.4300], NDCG [0.1506, 0.2815]


In [11]:
args.Ks = '[20, 50]'
predict(args)

2023-10-13 10:20:54,210 - root - INFO - n_users:           1835
2023-10-13 10:20:54,211 - root - INFO - n_items:           206
2023-10-13 10:20:54,211 - root - INFO - n_entities:        410
2023-10-13 10:20:54,212 - root - INFO - n_users_entities:  2245
2023-10-13 10:20:54,212 - root - INFO - n_relations:       24
2023-10-13 10:20:54,213 - root - INFO - n_h_list:          15046
2023-10-13 10:20:54,213 - root - INFO - n_t_list:          15046
2023-10-13 10:20:54,214 - root - INFO - n_r_list:          15046
2023-10-13 10:20:54,214 - root - INFO - n_cf_train:        5484
2023-10-13 10:20:54,215 - root - INFO - n_cf_test:         3661
2023-10-13 10:20:54,215 - root - INFO - n_kg_train:        15046
/home/user/ETRI-Recommender/data_loader/loader_kgat.py:118: RuntimeWarning: divide by zero encountered in power
  d_inv = np.power(rowsum, -1.0).flatten()
Evaluating Iteration: 100%|███████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 13.44it/s]

CF Evaluation: Precision [0.0584, 0.0307], Recall [0.5850, 0.7695], NDCG [0.3294, 0.3747]


# Post processing

In [7]:
import pandas as pd
import numpy as np

# Load the data from the text file into a DataFrame
df = pd.read_csv('datasets/culture/item_list.txt', sep=' ', header=None, names=['org_id', 'remap_id', 'freebase_id'])

# Create a dictionary that maps remap_id to org_id
id_dict = df.set_index('remap_id')['org_id'].to_dict()

def recommend_top_n(cf_scores, n):
    recommendations = {}
    for user_id, scores in enumerate(cf_scores):
        top_n_items = np.argsort(scores)[-1:-n-1:-1]
        # Replace the indices with the corresponding org_id
        recommendations[user_id] = [id_dict[str(item)] for item in top_n_items]
    return recommendations

cf_scores = np.load(args.save_dir + '/cf_scores.npy')
top_n_recommendations = recommend_top_n(cf_scores, n=20)

for user_id, items in top_n_recommendations.items():
    print(f"User {user_id} recommendations:\n{items}\n")


User 0 recommendations:
['기와20', '기와14', '기와19', '기와17', '기와18', '기와15', '의상36', '기와21', '의상35', '기와12', '의상37', '기와16', '도자27', '기와13', '기와22', '도자23', '기와1', '기와36', '가구39', '가구38']

User 1 recommendations:
['기와15', '기와12', '기와19', '기와14', '기와16', '기와18', '기와17', '도자27', '회화39', '기와20', '기와21', '기와11', '가구13', '의상37', '의상36', '기와5', '기와22', '의상38', '기와1', '가구39']

User 2 recommendations:
['기와18', '의상35', '의상37', '기와19', '의상38', '기와12', '기와15', '기와14', '기와20', '도자27', '기와21', '기와13', '회화39', '기와16', '기와22', '기와11', '도자23', '기와36', '의상11', '도자29']

User 3 recommendations:
['기와17', '기와19', '기와18', '기와14', '의상36', '의상35', '의상38', '기와21', '기와16', '기와15', '기와12', '도자27', '기와11', '기와22', '기와13', '도자23', '가구38', '회화27', '도자5', '가구39']

User 4 recommendations:
['기와19', '기와14', '기와12', '기와17', '회화39', '기와21', '기와20', '기와18', '기와13', '의상35', '도자27', '의상37', '기와11', '의상38', '기와22', '가구18', '가구39', '도자5', '기와5', '기와36']

User 5 recommendations:
['가구12', '가구19', '가구34', '가구15', '회화32', '가구23', '가구

In [8]:
df_5hop = pd.read_excel('datasets/culture/5hop.xlsx', skiprows=2)['5hop list']
rec_result=pd.DataFrame(top_n_recommendations).T

In [9]:
def remove(item) :
    return item.replace(',', '').replace(' ', '')

def color_cell(value1, value2):
    if value1 in value2:
        return 'background-color: yellow'  # You can change the background color as needed
    else:
        return ''
    
color_df = pd.DataFrame(index=rec_result.index, columns=rec_result.columns)

# Apply the function to the color_df
for i in range(len(rec_result.index)):
    for j in range(len(rec_result.columns)):
        color_df.iloc[i, j] = color_cell(rec_result.iloc[i, j], list(map(remove, df_5hop.iloc[i].split(', '))))

def apply_styles(val, style):
    return style

# Apply the styles to the DataFrame using the Styler.apply method
styled_df = rec_result.style.apply(apply_styles, style=color_df, axis=None)

styled_df

2023-10-11 12:14:55,191 - matplotlib - DEBUG - matplotlib data path: /home/user/anaconda3/lib/python3.9/site-packages/matplotlib/mpl-data
2023-10-11 12:14:55,194 - matplotlib - DEBUG - CONFIGDIR=/home/user/.config/matplotlib
2023-10-11 12:14:55,198 - matplotlib - DEBUG - interactive is False
2023-10-11 12:14:55,199 - matplotlib - DEBUG - platform is linux
2023-10-11 12:14:55,199 - matplotlib - DEBUG - loaded modules: ['sys', 'builtins', '_frozen_importlib', '_imp', '_thread', '_warnings', '_weakref', '_io', 'marshal', 'posix', '_frozen_importlib_external', 'time', 'zipimport', '_codecs', 'codecs', 'encodings.aliases', 'encodings', 'encodings.utf_8', '_signal', 'encodings.latin_1', '_abc', 'abc', 'io', '__main__', '_stat', 'stat', '_collections_abc', 'genericpath', 'posixpath', 'os.path', 'os', '_sitebuiltins', '_locale', '_bootlocale', '_distutils_hack', 'types', 'importlib._bootstrap', 'importlib._bootstrap_external', 'warnings', 'importlib', 'importlib.machinery', '_heapq', 'heapq', 

2023-10-11 12:14:55,282 - matplotlib - DEBUG - CACHEDIR=/home/user/.cache/matplotlib
2023-10-11 12:14:55,284 - matplotlib.font_manager - DEBUG - Using fontManager instance from /home/user/.cache/matplotlib/fontlist-v330.json
2023-10-11 12:14:55,549 - matplotlib.pyplot - DEBUG - Loaded backend module://matplotlib_inline.backend_inline version unknown.
2023-10-11 12:14:55,553 - matplotlib.pyplot - DEBUG - Loaded backend module://matplotlib_inline.backend_inline version unknown.


In [10]:
df_5hop_2 = pd.read_excel('datasets/culture/5hop.xlsx', skiprows=2).iloc[:, :11]

In [11]:
with pd.ExcelWriter("output.xlsx", engine='openpyxl') as writer:
    df_5hop_2.to_excel(writer, sheet_name='Data', index=False)

    # Get the ExcelWriter object's workbook and add the styled DataFrame to the same sheet in the next columns
    workbook = writer.book
    styled_df.to_excel(writer, sheet_name='Data', startcol=len(df_5hop_2.columns), index=False)